<img align="left" src="https://lever-client-logos.s3.amazonaws.com/864372b1-534c-480e-acd5-9711f850815c-1524247202159.png" width=200>
<br></br>
<br></br>

# Sprint Challenge
## *Data Science Unit 4 Sprint 1*

After a week of Natural Language Processing, you've learned some cool new stuff: how to process text, how turn text into vectors, and how to model topics from documents. Apply your newly acquired skills to one of the most famous NLP datasets out there: [Yelp](https://www.yelp.com/dataset/challenge). As part of the job selection process, some of my friends have been asked to create analysis of this dataset, so I want to empower you to have a head start.  

The real dataset is massive (almost 8 gigs uncompressed). I've sampled the data for you to something more managable for the Sprint Challenge. You can analyze the full dataset as a stretch goal or after the sprint challenge. As you work on the challenge, I suggest adding notes about your findings and things you want to analyze in the future.

## Challenge Objectives
*Successfully complete these all these objectives to earn a 2. There are more details on each objective further down in the notebook.*
* <a href="#p1">Part 1</a>: Write a function to tokenize the yelp reviews
* <a href="#p2">Part 2</a>: Create a vector representation of those tokens
* <a href="#p3">Part 3</a>: Use your tokens in a classification model on yelp rating
* <a href="#p4">Part 4</a>: Estimate & Interpret a topic model of the Yelp reviews

In [114]:
import pandas as pd

yelp = pd.read_json('./data/review_sample.json', lines=True)

In [115]:
yelp.head()

business_id  cool                date  funny  \
0  nDuEqIyRc8YKS1q1fX0CZg     1 2015-03-31 16:50:30      0   
1  eMYeEapscbKNqUDCx705hg     0 2015-12-16 05:31:03      0   
2  6Q7-wkCPc1KF75jZLOTcMw     1 2010-06-20 19:14:48      1   
3  k3zrItO4l9hwfLRwHBDc9w     3 2010-07-13 00:33:45      4   
4  6hpfRwGlOzbNv7k5eP9rsQ     1 2018-06-30 02:30:01      0   

                review_id  stars  \
0  eZs2tpEJtXPwawvHnHZIgQ      1   
1  DoQDWJsNbU0KL1O29l_Xug      4   
2  DDOdGU7zh56yQHmUnL1idQ      3   
3  LfTMUWnfGFMOfOIyJcwLVA      1   
4  zJSUdI7bJ8PNJAg4lnl_Gg      4   

                                                text  useful  \
0  BEWARE!!! FAKE, FAKE, FAKE....We also own a sm...      10   
1  Came here for lunch Togo. Service was quick. S...       0   
2  I've been to Vegas dozens of times and had nev...       2   
3  We went here on a night where they closed off ...       5   
4  3.5 to 4 stars\n\nNot bad for the price, $12.9...       5   

                  user_id  
0  n1LM36qNg4rqGXIcvVXv8w  
1  5CgjjDAic2-FAvCtiHpytA  
2  BdV-cf3LScmb8kZ7iiBcMA  
3  cZZnBqh4gAEy4CdNvJailQ  
4  n9QO4ClYAS7h9fpQwa5bhA

In [116]:
yelp.dtypes

business_id            object
cool                    int64
date           datetime64[ns]
funny                   int64
review_id              object
stars                   int64
text                   object
useful                  int64
user_id                object
dtype: object

## Part 1: Tokenize Function
<a id="#p1"></a>

Complete the function `tokenize`. Your function should
- accept one document at a time
- return a list of tokens

You are free to use any method you have learned this week.

In [117]:
import numpy as np
import gensim
import re

from gensim.utils import simple_preprocess
from gensim.parsing.preprocessing import STOPWORDS
from gensim.models.ldamulticore import LdaMulticore

def tokenize(doc):
    return [token for token in simple_preprocess(doc) if token not in STOPWORDS]

In [118]:
def stringify(stringlist):
    return " ".join(stringlist)

## Part 2: Vector Representation
<a id="#p2"></a>
1. Create a vector representation of the reviews
2. Write a fake review and query for the 10 most similiar reviews, print the text of the reviews. Do you notice any patterns?
    - Given the size of the dataset, it will probably be best to use a `NearestNeighbors` model for this. 

In [119]:
from sklearn.feature_extraction.text import TfidfVectorizer

# instantiate vectorizer
tfidf = TfidfVectorizer()

In [120]:
# tokenize the reviews
yelp['text'] = yelp['text'].apply(tokenize)
yelp['text'] = yelp['text'].apply(stringify)
yelp['text'].head()

0    beware fake fake fake small business los alami...
1    came lunch togo service quick staff friendly c...
2    ve vegas dozens times stepped foot circus circ...
3    went night closed street party best actually g...
4    stars bad price lunch seniors pay eating hot f...
Name: text, dtype: object

In [121]:

# fit the vectorizer
tfidf.fit(yelp['text'])

# create document term matrix
dtm = tfidf.transform(yelp['text'])

# make dtm a dataframe
dtm = pd.DataFrame(dtm.todense(), columns=tfidf.get_feature_names())

dtm.head()

aa  aaa  aaaahhhs  aaasssk  aabs  aamco  aand  aaron  aback  abandoned  \
0  0.0  0.0       0.0      0.0   0.0    0.0   0.0    0.0    0.0        0.0   
1  0.0  0.0       0.0      0.0   0.0    0.0   0.0    0.0    0.0        0.0   
2  0.0  0.0       0.0      0.0   0.0    0.0   0.0    0.0    0.0        0.0   
3  0.0  0.0       0.0      0.0   0.0    0.0   0.0    0.0    0.0        0.0   
4  0.0  0.0       0.0      0.0   0.0    0.0   0.0    0.0    0.0        0.0   

   ...  覺得店家很用心製作  誓約書にサイン  誰も乗車しなくても  豆腐花  車好きさんには  這是一個不錯的選擇  運転しない  \
0  ...        0.0      0.0        0.0  0.0      0.0        0.0    0.0   
1  ...        0.0      0.0        0.0  0.0      0.0        0.0    0.0   
2  ...        0.0      0.0        0.0  0.0      0.0        0.0    0.0   
3  ...        0.0      0.0        0.0  0.0      0.0        0.0    0.0   
4  ...        0.0      0.0        0.0  0.0      0.0        0.0    0.0   

   運転中も英語で指導があります  食べ物はうまい  餐後點了甜點  
0             0.0      0.0     0.0  
1             0.0      0.0     0.0  
2             0.0      0.0     0.0  
3             0.0      0.0     0.0  
4             0.0      0.0     0.0  

[5 rows x 26475 columns]

In [122]:
from sklearn.neighbors import NearestNeighbors

nn = NearestNeighbors(n_neighbors=10, algorithm='kd_tree')
nn.fit(dtm)

NearestNeighbors(algorithm='kd_tree', leaf_size=30, metric='minkowski',
         metric_params=None, n_jobs=None, n_neighbors=10, p=2, radius=1.0)

In [123]:
# fake yelp review
fake = ["This place is the pits The food was cold the server was sassy in a bad way and the decor reminded me of childhood memories that I drink to forget Never coming back"]

new = tfidf.transform(fake)
nn.kneighbors(new.todense())

(array([[1.30681814, 1.31305323, 1.31354937, 1.31899514, 1.32049106,
         1.32211099, 1.32276671, 1.32506046, 1.32532111, 1.32711741]]),
 array([[2042, 4599, 3434,  150, 7662, 7089, 4727, 8786, 2990, 7680]],
       dtype=int64))

In [35]:
bad_neighbors = [6311, 6204, 2042, 4599, 3434,  150, 7662, 7089, 4727, 8786]

for i in bad_neighbors:
    print("-----\n", yelp.text[i], "\n")

-----
  

-----
  

-----
 was amazing comfort food we were party of and every dish we ordered was on point excellent service must try do not forget to order specialty drink delicious 

-----
 only word describes this place yuck bad food bad beer bad service bad atmosphere 

-----
 love this place so charming and love to see all the candies from my childhood however the soda selection and the taffy wall are the highlights for me personally 

-----
 service is my number one priority we had to wait minutes just to get seated during very slow lunch hour server missed few things and had to be reminded food was not very good but really liked the hot salsa that came with the chips prior to our food arriving it was very good spice level for me bland place at best 

-----
 this is one of my favorite spots to go for sushi or really any japanese food their ramen is delicious this place is byob which makes it fun place to go with group just keep in mind it gets busy so if you re group is too larg

In [ ]:
"""
Observations:

We get a lot of reviews about service and decor here. But unlike my fake review, 
some of them are favorable.
7089 seems to only be there because of the word "server".
8786 bears little resemblance to my fake review.

"""

## Part 3: Classification
<a id="#p3"></a>
Your goal in this section will be to predict `stars` from the review dataset. 

1. Create a piepline object with a sklearn `CountVectorizer` or `TfidfVector` and any sklearn classifier. Use that pipeline to estimate a model to predict `stars`. Use the Pipeline to predict a star rating for your fake review from Part 2. 
2. Tune the entire pipeline with a GridSearch

In [124]:
from sklearn.pipeline import Pipeline
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import GridSearchCV

rfc = RandomForestClassifier()

In [125]:
pipe = Pipeline([
                ('tfidf', tfidf),
                ('rfc', rfc)
                    ])

In [126]:
len(yelp)

10000

In [47]:
batch_params = []

In [44]:
params = {
    'tfidf__max_df': ( 0.75, 0.8, 0.9, 1.0),
    'tfidf__min_df': (.01, .02, .05, .1),
    'tfidf__max_features': (300, 500, 700, 1000),
    'rfc__n_estimators':(5, 10, 20, 25),
    'rfc__max_depth':(15,20, 30)
}

grid_search = GridSearchCV(pipe, params, cv=5, n_jobs=6, verbose=1)
grid_search.fit(yelp.text, yelp.stars)

Fitting 5 folds for each of 768 candidates, totalling 3840 fits


[Parallel(n_jobs=6)]: Using backend LokyBackend with 6 concurrent workers.
[Parallel(n_jobs=6)]: Done  38 tasks      | elapsed:   11.3s
[Parallel(n_jobs=6)]: Done 188 tasks      | elapsed:   54.8s
[Parallel(n_jobs=6)]: Done 438 tasks      | elapsed:  2.1min
[Parallel(n_jobs=6)]: Done 788 tasks      | elapsed:  4.1min
[Parallel(n_jobs=6)]: Done 1238 tasks      | elapsed:  6.6min
[Parallel(n_jobs=6)]: Done 1788 tasks      | elapsed:  9.5min
[Parallel(n_jobs=6)]: Done 2438 tasks      | elapsed: 13.3min
[Parallel(n_jobs=6)]: Done 3188 tasks      | elapsed: 17.4min
[Parallel(n_jobs=6)]: Done 3840 out of 3840 | elapsed: 22.0min finished


GridSearchCV(cv=5, error_score='raise-deprecating',
       estimator=Pipeline(memory=None,
     steps=[('tfidf', TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.float64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=1.0, max_features=None, min_df=1,
        ngram_range=(1, 1), norm='l2', preprocessor=None, smooth_idf=True,...obs=None,
            oob_score=False, random_state=None, verbose=0,
            warm_start=False))]),
       fit_params=None, iid='warn', n_jobs=6,
       param_grid={'tfidf__max_df': (0.75, 0.8, 0.9, 1.0), 'tfidf__min_df': (0.01, 0.02, 0.05, 0.1), 'tfidf__max_features': (300, 500, 700, 1000), 'rfc__n_estimators': (5, 10, 20, 25), 'rfc__max_depth': (15, 20, 30)},
       pre_dispatch='2*n_jobs', refit=True, return_train_score='warn',
       scoring=None, verbose=1)

In [45]:
print(grid_search.best_score_)
print(grid_search.predict(fake))

0.5658
[1]


In [50]:
batch_params.append((grid_search.best_score_, grid_search.best_params_))

In [141]:
batch_params

[(0.5658,
  {'rfc__max_depth': 30,
   'rfc__n_estimators': 25,
   'tfidf__max_df': 0.9,
   'tfidf__max_features': 1000,
   'tfidf__min_df': 0.01}),
 (0.5658,
  {'rfc__max_depth': 30,
   'rfc__n_estimators': 25,
   'tfidf__max_df': 0.9,
   'tfidf__max_features': 1000,
   'tfidf__min_df': 0.01})]

In [ ]:
"""
Not sure we'll get a better result than that. 
At least it scored my fake review appropriately, and it beats the baseline score  of .2
"""

## Part 4: Topic Modeling

Let's find out what those yelp reviews are saying! :D

1. Estimate a LDA topic model of the review text
    - Keep the `iterations` parameter at or below 5 to reduce run time
    - The `workers` parameter should match the number of physical cores on your machine.
2. Create 1-2 visualizations of the results
    - You can use the most important 3 words of a topic in relevant visualizations. Refer to yesterday's notebook to extract. 
3. In markdown, write 1-2 paragraphs of analysis on the results of your topic model

__*Note*__: You can pass the DataFrame column of text reviews to gensim. You do not have to use a generator.

In [127]:
from gensim import corpora
from gensim.models import LdaMulticore
from gensim.corpora import Dictionary

Learn the vocubalary of the yelp data:

In [128]:
def doc_stream(df):
    for index, row in df.iterrows():
        yield row['text'].split(' ')
        
streaming_data = doc_stream(yelp)

In [129]:
id2word = corpora.Dictionary(streaming_data)
id2word.filter_extremes(no_below=10, no_above=0.75)

Create a bag of words representation of the entire corpus

In [130]:
streaming_data = doc_stream(yelp)
corpus = [id2word.doc2bow(text) for text in streaming_data]

In [133]:
id2word.token2id['decor']

1502

Your LDA model should be ready for estimation: 

In [137]:
lda = LdaMulticore(corpus=corpus,
                   id2word=id2word,
                   iterations=5,
                   passes=10,
                   workers=6,
                   num_topics = 4
                  )

C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * log

C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * log

C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * log

C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * log

C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * log

...

C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * log

C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * log

C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * log

C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * log

C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\gensim\models\ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * log

Create 1-2 visualizations of the results

In [138]:
lda.print_topics()

[(0,
  '0.016*"food" + 0.016*"good" + 0.015*"service" + 0.011*"like" + 0.009*"great" + 0.009*"place" + 0.007*"time" + 0.005*"went" + 0.005*"come" + 0.005*"amazing"'),
 (1,
  '0.016*"food" + 0.014*"good" + 0.014*"great" + 0.009*"place" + 0.007*"like" + 0.007*"chicken" + 0.006*"ordered" + 0.006*"restaurant" + 0.006*"delicious" + 0.006*"service"'),
 (2,
  '0.011*"place" + 0.010*"great" + 0.009*"service" + 0.008*"like" + 0.008*"good" + 0.007*"time" + 0.006*"got" + 0.005*"nice" + 0.005*"food" + 0.005*"definitely"'),
 (3,
  '0.017*"place" + 0.014*"time" + 0.009*"food" + 0.007*"like" + 0.007*"good" + 0.007*"ve" + 0.006*"got" + 0.006*"great" + 0.006*"service" + 0.006*"love"')]

In [139]:
# Visualize

import pyLDAvis.gensim

pyLDAvis.enable_notebook()
pyLDAvis.gensim.prepare(lda, corpus, id2word)

C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\pyLDAvis\_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
1      0.061427 -0.003402       1        1  32.111851
2     -0.035997  0.007414       2        1  23.663963
3     -0.026886 -0.016997       3        1  22.832781
0      0.001455  0.012985       4        1  21.391405, topic_info=     Category         Freq          Term        Total  loglift  logprob
42    Default  3600.000000       service  3600.000000  30.0000  30.0000
31    Default  3349.000000          time  3349.000000  29.0000  29.0000
133   Default  5070.000000          food  5070.000000  28.0000  28.0000
122   Default  4734.000000         place  4734.000000  27.0000  27.0000
37    Default  4790.000000          good  4790.000000  26.0000  26.0000
465   Default   942.000000          told   942.000000  25.0000  25.0000
309   Default   863.000000        cheese   863.000000  24.0000  24.0000
1667  Default   594.000000           car   594.000000  23.0000  23.0000
2241  Default   215.000000            la   215.000000  22.0000  22.0000
94    Default   911.000000          room   911.000000  21.0000  21.0000
353   Default   885.000000         sauce   885.000000  20.0000  20.0000
189   Default   392.000000          hair   392.000000  19.0000  19.0000
392   Default   850.000000      customer   850.000000  18.0000  18.0000
473   Default   915.000000          work   915.000000  17.0000  17.0000
1736  Default   570.000000        burger   570.000000  16.0000  16.0000
580   Default   733.000000        drinks   733.000000  15.0000  15.0000
638   Default  1671.000000          love  1671.000000  14.0000  14.0000
27    Default  1176.000000          said  1176.000000  13.0000  13.0000
1039  Default  1452.000000       chicken  1452.000000  12.0000  12.0000
1690  Default   324.000000  professional   324.000000  11.0000  11.0000
393   Default  1178.000000           day  1178.000000  10.0000  10.0000
15    Default  3502.000000          like  3502.000000   9.0000   9.0000
106   Default  1459.000000          went  1459.000000   8.0000   8.0000
515   Default   471.000000           job   471.000000   7.0000   7.0000
2225  Default   393.000000         spicy   393.000000   6.0000   6.0000
570   Default  1479.000000    restaurant  1479.000000   5.0000   5.0000
254   Default   175.000000         nails   175.000000   4.0000   4.0000
318   Default  1290.000000     delicious  1290.000000   3.0000   3.0000
8     Default   363.000000       company   363.000000   2.0000   2.0000
1246  Default   635.000000         fries   635.000000   1.0000   1.0000
...       ...          ...           ...          ...      ...      ...
15     Topic4   975.817810          like  3502.770752   0.2641  -4.5378
937    Topic4   304.933289      location   845.084839   0.5228  -5.7010
176    Topic4   412.078979       amazing  1323.790161   0.3751  -5.3999
655    Topic4   226.076248        things   586.760803   0.5884  -6.0002
311    Topic4   431.415833          come  1438.794434   0.3377  -5.3540
106    Topic4   432.620575          went  1459.151123   0.3264  -5.3512
54     Topic4   231.443222         check   620.240906   0.5564  -5.9767
78     Topic4   265.461029          long   762.183838   0.4875  -5.8396
85     Topic4   305.669983         night   939.657898   0.4192  -5.6986
634    Topic4   258.841248          home   756.046631   0.4703  -5.8649
125    Topic4   271.604828           bad   817.793823   0.4399  -5.8167
99     Topic4   301.329010          sure   952.886475   0.3909  -5.7129
1046   Topic4   260.142944           lot   777.201721   0.4477  -5.8598
188    Topic4   831.446472         great  4318.496582  -0.1053  -4.6979
122    Topic4   821.279175         place  4734.791992  -0.2096  -4.7102
31     Topic4   647.606506          time  3349.233154  -0.1010  -4.9478
105    Topic4   271.870911         vegas   896.204895   0.3493  -5.8158
46     Topic4   235.137131          area   752.534607   0.3789  -5.9609
393    Topic4   301.075989       

In [153]:
"""
Topics and terms they own at least one quarter of:
1 - Sauce, cheese, msuc, fresh, small, pizza, chicken, delicious
2 - Car, said, try, minutes, customer, room, people, nice
3 - Told, love, staff, day, new, right, asked
4 - Clean, location, night, drinks, room, bar, come


So the topics are, broadly speaking:
1: Food quality
2: Social atmosphere
3: Service quality
4: Night life
"""

'\nTopics and terms they own at least one quarter of:\n1 - Sauce, cheese, msuc, fresh, small, pizza, chicken, delicious\n2 - Car, said, try, minutes, customer, room, people, nice\n3 - Told, love, staff, day, new, right, asked\n4 - Clean, location, night, drinks, room, bar, come\n\n\nSo the topics are, broadly speaking:\n1: Food quality\n2: Social atmosphere\n3: Service quality\n4: Night life\n'

## Stretch Goals

Complete one of more of these to push your score towards a three: 
* Incorporate named entity recognition into your analysis
* Compare vectorization methods in the classification section
* [x] Analyze more (or all) of the yelp dataset - this one is v. hard. 
* [x] Use a generator object on the reviews file - this would help you with the analyzing the whole dataset.
* Incorporate any of the other yelp dataset entities in your analysis (business, users, etc.)

In [142]:
batch_params

[(0.5658,
  {'rfc__max_depth': 30,
   'rfc__n_estimators': 25,
   'tfidf__max_df': 0.9,
   'tfidf__max_features': 1000,
   'tfidf__min_df': 0.01}),
 (0.5658,
  {'rfc__max_depth': 30,
   'rfc__n_estimators': 25,
   'tfidf__max_df': 0.9,
   'tfidf__max_features': 1000,
   'tfidf__min_df': 0.01})]

In [150]:
# small grid searches for RFC models predicting usefulness, funniness, and coolness of a review
# few params for the sake of time

params = {
    'tfidf__max_df': (0.9, 1.0),
    'tfidf__min_df': (.01, .02),
    'tfidf__max_features': (700, 1000),
    'rfc__n_estimators':(20, 25),
    'rfc__max_depth':(20, 30)
}



In [146]:
cool = GridSearchCV(pipe, params, cv=5, n_jobs=6, verbose=1)
cool.fit(yelp.text, yelp.cool)

Fitting 5 folds for each of 32 candidates, totalling 160 fits


C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\sklearn\model_selection\_split.py:652: Warning: The least populated class in y has only 1 members, which is too few. The minimum number of members in any class cannot be less than n_splits=5.
  % (min_groups, self.n_splits)), Warning)
[Parallel(n_jobs=6)]: Using backend LokyBackend with 6 concurrent workers.
[Parallel(n_jobs=6)]: Done  38 tasks      | elapsed:   11.5s
[Parallel(n_jobs=6)]: Done 160 out of 160 | elapsed:   46.3s finished


GridSearchCV(cv=5, error_score='raise-deprecating',
       estimator=Pipeline(memory=None,
     steps=[('tfidf', TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.float64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=1.0, max_features=None, min_df=1,
        ngram_range=(1, 1), norm='l2', preprocessor=None, smooth_idf=True,...obs=None,
            oob_score=False, random_state=None, verbose=0,
            warm_start=False))]),
       fit_params=None, iid='warn', n_jobs=6,
       param_grid={'tfidf__max_df': (0.9, 1.0), 'tfidf__min_df': (0.01, 0.02), 'tfidf__max_features': (700, 1000), 'rfc__n_estimators': (20, 25), 'rfc__max_depth': (20, 30)},
       pre_dispatch='2*n_jobs', refit=True, return_train_score='warn',
       scoring=None, verbose=1)

In [147]:
funny = GridSearchCV(pipe, params, cv=5, n_jobs=6, verbose=1)
funny.fit(yelp.text, yelp.funny)

Fitting 5 folds for each of 32 candidates, totalling 160 fits


C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\sklearn\model_selection\_split.py:652: Warning: The least populated class in y has only 1 members, which is too few. The minimum number of members in any class cannot be less than n_splits=5.
  % (min_groups, self.n_splits)), Warning)
[Parallel(n_jobs=6)]: Using backend LokyBackend with 6 concurrent workers.
[Parallel(n_jobs=6)]: Done  38 tasks      | elapsed:   10.1s
[Parallel(n_jobs=6)]: Done 160 out of 160 | elapsed:   43.7s finished


GridSearchCV(cv=5, error_score='raise-deprecating',
       estimator=Pipeline(memory=None,
     steps=[('tfidf', TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.float64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=1.0, max_features=None, min_df=1,
        ngram_range=(1, 1), norm='l2', preprocessor=None, smooth_idf=True,...obs=None,
            oob_score=False, random_state=None, verbose=0,
            warm_start=False))]),
       fit_params=None, iid='warn', n_jobs=6,
       param_grid={'tfidf__max_df': (0.9, 1.0), 'tfidf__min_df': (0.01, 0.02), 'tfidf__max_features': (700, 1000), 'rfc__n_estimators': (20, 25), 'rfc__max_depth': (20, 30)},
       pre_dispatch='2*n_jobs', refit=True, return_train_score='warn',
       scoring=None, verbose=1)

In [148]:
useful = GridSearchCV(pipe, params, cv=5, n_jobs=6, verbose=1)
useful.fit(yelp.text, yelp.useful)

Fitting 5 folds for each of 32 candidates, totalling 160 fits


C:\Users\Cooper\Anaconda3\envs\Mike\lib\site-packages\sklearn\model_selection\_split.py:652: Warning: The least populated class in y has only 1 members, which is too few. The minimum number of members in any class cannot be less than n_splits=5.
  % (min_groups, self.n_splits)), Warning)
[Parallel(n_jobs=6)]: Using backend LokyBackend with 6 concurrent workers.
[Parallel(n_jobs=6)]: Done  38 tasks      | elapsed:   11.2s
[Parallel(n_jobs=6)]: Done 160 out of 160 | elapsed:   51.1s finished


GridSearchCV(cv=5, error_score='raise-deprecating',
       estimator=Pipeline(memory=None,
     steps=[('tfidf', TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.float64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=1.0, max_features=None, min_df=1,
        ngram_range=(1, 1), norm='l2', preprocessor=None, smooth_idf=True,...obs=None,
            oob_score=False, random_state=None, verbose=0,
            warm_start=False))]),
       fit_params=None, iid='warn', n_jobs=6,
       param_grid={'tfidf__max_df': (0.9, 1.0), 'tfidf__min_df': (0.01, 0.02), 'tfidf__max_features': (700, 1000), 'rfc__n_estimators': (20, 25), 'rfc__max_depth': (20, 30)},
       pre_dispatch='2*n_jobs', refit=True, return_train_score='warn',
       scoring=None, verbose=1)

In [149]:
print(cool.best_score_)
print(funny.best_score_)
print(useful.best_score_)

0.7515
0.7929
0.5258


In [154]:
"""
Nice! Beats the baseline for all of these.
We can pretty well predict usefulness, coolness, and funniness of a review from its text.

Now I need to catch a plane.
"""

'\nNice! Beats the baseline for all of these.\nWe can pretty well predict usefulness, coolness, and funniness of a review from its text.\n\nNow I need to catch a plane.\n'